<img src="https://tradingcomdados.com/images/logotipo/logotipo-trading-com-dados.svg" width="300" align="left"/>

------
# **Fabuloso 4**

### Backtesting e algotrading

------

# 1. Bibliotecas

In [ ]:
%pip install MetaTrader5
%pip install ta
%pip install vectorbt

In [47]:
# Análise e manipulação de dados
import numpy as np
import pandas as pd

# Dados séries temporais
from datetime import datetime, timedelta
import pytz
from time import sleep

# Integração com MetaTrader 5
import MetaTrader5 as mt5

# Indicadores e backtesting
import ta
import vectorbt as vbt

# Bibliotecas gráficas
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# 2.Obtenção de dados

## 2.1. Cotações OHLC

In [48]:
mt5.initialize()

True

In [49]:
lista_tickers = ['WDO$', 'WIN$']

In [50]:
mt5.TIMEFRAME_D1

16408

In [51]:
# Observe que os timeframes são do tipo "int"
print(mt5.TIMEFRAME_D1)
print(mt5.TIMEFRAME_H1)
print(mt5.TIMEFRAME_M15)
print(mt5.TIMEFRAME_M10)
print(mt5.TIMEFRAME_M5)
print(mt5.TIMEFRAME_M1)

timeframes = [16408, 16385, 15, 10, 5, 1]

16408
16385
15
10
5
1


In [52]:
timezone = pytz.timezone("America/Sao_Paulo")
data_inicio = datetime.now() - timedelta(days=10000)
data_fim = datetime.now()

cotacoes_mt5_all = []

for ticker in lista_tickers:

    cotacoes_mt5_ativo = []

    for timeframe in timeframes:

        cotacoes_mt5_ticker = mt5.copy_rates_range(ticker, timeframe, data_inicio, data_fim)
        cotacoes_mt5_ticker = pd.DataFrame(cotacoes_mt5_ticker)
        cotacoes_mt5_ticker['ticker'] = str(ticker)

        if timeframe==16408:
            cotacoes_mt5_ticker['timeframe'] = '1D'
        elif timeframe==16385:
            cotacoes_mt5_ticker['timeframe'] = '1H'
        else:
            cotacoes_mt5_ticker['timeframe'] = str(timeframe)+'M'
        
        cotacoes_mt5_ticker.index = pd.to_datetime(cotacoes_mt5_ticker['time'], unit='s')
        cotacoes_mt5_ticker = cotacoes_mt5_ticker.drop('time', axis=1)
        cotacoes_mt5_ativo.append(cotacoes_mt5_ticker)
    
    cotacoes_mt5_all.append(cotacoes_mt5_ativo)

In [53]:
list(enumerate(lista_tickers))

[(0, 'WDO$'), (1, 'WIN$')]

In [54]:
timeframes_str = ['1D', '1H', '15M', '10M', '5M', '1M']
list(enumerate(timeframes_str))

[(0, '1D'), (1, '1H'), (2, '15M'), (3, '10M'), (4, '5M'), (5, '1M')]

In [55]:
cotacoes_mt5_all[1][4]

open      high       low     close  tick_volume  \
time                                                                       
2018-02-15 09:00:00  113824.0  113944.0  113610.0  113610.0         4302   
2018-02-15 09:05:00  113610.0  113704.0  113483.0  113584.0         5683   
2018-02-15 09:10:00  113584.0  113777.0  113483.0  113610.0         6170   
2018-02-15 09:15:00  113610.0  113657.0  113437.0  113497.0         6194   
2018-02-15 09:20:00  113490.0  113731.0  113477.0  113557.0         5749   
...                       ...       ...       ...       ...          ...   
2023-03-17 17:35:00  102935.0  102955.0  102855.0  102925.0         5802   
2023-03-17 17:40:00  102930.0  102940.0  102860.0  102880.0         3766   
2023-03-17 17:45:00  102885.0  102910.0  102645.0  102750.0         7666   
2023-03-17 17:50:00  102745.0  102830.0  102670.0  102700.0         4151   
2023-03-17 18:00:00  102630.0  102630.0  102630.0  102630.0           14   

                     spread  real_volume ticker timeframe  
time                                                       
2018-02-15 09:00:00       1        15773   WIN$        5M  
2018-02-15 09:05:00       1        16888   WIN$        5M  
2018-02-15 09:10:00       1        18231   WIN$        5M  
2018-02-15 09:15:00       1        18035   WIN$        5M  
2018-02-15 09:20:00       1        15251   WIN$        5M  
...                     ...          ...    ...       ...  
2023-03-17 17:35:00       0        63272   WIN$        5M  
2023-03-17 17:40:00       0        36456   WIN$        5M  
2023-03-17 17:45:00       0        83906   WIN$        5M  
2023-03-17 17:50:00       0        35767   WIN$        5M  
2023-03-17 18:00:00       0        12125   WIN$        5M  

[136962 rows x 9 columns]

## 2.2. Cálculo indicadores

In [58]:
periodo_indicadores = 5
desv_pad = 1.5

In [59]:
for i in range(len(cotacoes_mt5_all)):
    for j in range(len(cotacoes_mt5_ativo)):
        cotacoes_mt5_all[i][j]['RSI'] = ta.momentum.RSIIndicator(cotacoes_mt5_all[i][j].close, window=periodo_indicadores).rsi()
        cotacoes_mt5_all[i][j]['Bol_sup'] = ta.volatility.BollingerBands(cotacoes_mt5_all[i][j].RSI, window=periodo_indicadores, window_dev=desv_pad).bollinger_hband()
        cotacoes_mt5_all[i][j]['Bol_inf'] = ta.volatility.BollingerBands(cotacoes_mt5_all[i][j].RSI, window=periodo_indicadores, window_dev=desv_pad).bollinger_lband()
        cotacoes_mt5_all[i][j]['Bol_media'] = ta.volatility.BollingerBands(cotacoes_mt5_all[i][j].RSI, window=periodo_indicadores, window_dev=desv_pad).bollinger_mavg()

# 3. Backtesting

In [60]:
for i in range(len(cotacoes_mt5_all)):
    for j in range(len(cotacoes_mt5_ativo)):

        if j == 0:
            cotacoes_mt5_all[i][j]['entrada'] = cotacoes_mt5_all[i][j]['RSI'].vbt.crossed_above(cotacoes_mt5_all[i][j]['Bol_sup'])
            cotacoes_mt5_all[i][j]['saida'] = cotacoes_mt5_all[i][j]['RSI'].vbt.crossed_below(cotacoes_mt5_all[i][j]['Bol_media'])
        else:
            cotacoes_mt5_all[i][j]['entrada'] = cotacoes_mt5_all[i][j]['RSI'].vbt.crossed_above(cotacoes_mt5_all[i][j]['Bol_sup']).vbt.signals.AND(cotacoes_mt5_all[i][j].index.hour <= 16)
            cotacoes_mt5_all[i][j]['saida'] = cotacoes_mt5_all[i][j]['RSI'].vbt.crossed_below(cotacoes_mt5_all[i][j]['Bol_inf']).vbt.signals.OR(cotacoes_mt5_all[i][j].index.hour >= 17)


In [61]:
ls_backtests_all = []

for i in range(len(cotacoes_mt5_all)):

    ls_backtests_ativo = []

    for j in range(len(cotacoes_mt5_ativo)):

        backtest_ativo = vbt.Portfolio.from_signals(cotacoes_mt5_all[i][j].close, cotacoes_mt5_all[i][j].entrada, cotacoes_mt5_all[i][j].saida, direction='both')
        ls_backtests_ativo.append(backtest_ativo)
    
    ls_backtests_all.append(ls_backtests_ativo)

In [62]:
for i in range(len(ls_backtests_all)):

    for j in range(len(ls_backtests_ativo)):

        print('Ativo', list(enumerate(lista_tickers))[i][1], 'no timeframe',list(enumerate(timeframes_str))[j][1], 'teve retorno de', ls_backtests_all[i][j].total_return())


Ativo WDO$ no timeframe 1D teve retorno de -0.3560373780687797
Ativo WDO$ no timeframe 1H teve retorno de -0.1930888069684359
Ativo WDO$ no timeframe 15M teve retorno de -0.4689108044125576
Ativo WDO$ no timeframe 10M teve retorno de -0.5390288811761416
Ativo WDO$ no timeframe 5M teve retorno de -0.4277710000838394
Ativo WDO$ no timeframe 1M teve retorno de -0.8477164313428748
Ativo WIN$ no timeframe 1D teve retorno de -0.5993767552084389
Ativo WIN$ no timeframe 1H teve retorno de -0.18283713413143857
Ativo WIN$ no timeframe 15M teve retorno de -0.00486711757917945
Ativo WIN$ no timeframe 10M teve retorno de 0.27640922062525247
Ativo WIN$ no timeframe 5M teve retorno de -0.5029234628099027
Ativo WIN$ no timeframe 1M teve retorno de -0.4571643634363208


In [63]:
ls_backtests_all[0][1].plot().show()

In [64]:
ls_backtests_all[0][1].stats()

c:\Users\jamir\AppData\Local\Programs\Python\Python310\lib\site-packages\vectorbt\generic\stats_builder.py:396: UserWarning:

Metric 'sharpe_ratio' requires frequency to be set

c:\Users\jamir\AppData\Local\Programs\Python\Python310\lib\site-packages\vectorbt\generic\stats_builder.py:396: UserWarning:

Metric 'calmar_ratio' requires frequency to be set

c:\Users\jamir\AppData\Local\Programs\Python\Python310\lib\site-packages\vectorbt\generic\stats_builder.py:396: UserWarning:

Metric 'omega_ratio' requires frequency to be set

c:\Users\jamir\AppData\Local\Programs\Python\Python310\lib\site-packages\vectorbt\generic\stats_builder.py:396: UserWarning:

Metric 'sortino_ratio' requires frequency to be set



Start                         2018-02-28 09:00:00
End                           2023-03-17 17:00:00
Period                                      11698
Start Value                                 100.0
End Value                               80.691119
Total Return [%]                       -19.308881
Benchmark Return [%]                    32.702624
Max Gross Exposure [%]                      100.0
Total Fees Paid                               0.0
Max Drawdown [%]                        44.402173
Max Drawdown Duration                      5279.0
Total Trades                                 1605
Total Closed Trades                          1604
Total Open Trades                               1
Open Trade PnL                                0.0
Win Rate [%]                            46.321696
Best Trade [%]                             5.5359
Worst Trade [%]                         -6.624938
Avg Winning Trade [%]                    0.698264
Avg Losing Trade [%]                    -0.624997
